In [1]:

# load data
from sentence_transformers import SentenceTransformer
from twitter.data.loader.prepro import get_user, get_cleaned_tweets

from bertopic import BERTopic

model = SentenceTransformer('paraphrase-MiniLM-L3-v2')


data = get_cleaned_tweets("BabakShekarabi")


2023-04-09 13:44:50.202860: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-04-09 13:44:51.426220: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
2023-04-09 13:44:53.675486: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:997] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2023-04-09 13:44:53.703944: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:997] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA n

In [4]:
#data = get_cleaned_tweets("BabakShekarabi")

topic_model = BERTopic(embedding_model=model, calculate_probabilities=True, verbose=True)
topics, probabilities = topic_model.fit_transform(data)


Batches:   0%|          | 0/219 [00:00<?, ?it/s]

2023-04-09 13:45:56,250 - BERTopic - Transformed documents to Embeddings
2023-04-09 13:46:24,326 - BERTopic - Reduced dimensionality
2023-04-09 13:46:26,732 - BERTopic - Clustered reduced embeddings


In [5]:
topic_model.visualize_topics()

In [8]:
embeddings = model.encode(data, show_progress_bar=False)

Index(['tweets_count', 'retweets_count', 'likes_count', 'date', 'user',
       'user_id', 'created', 'descriptionLinks', 'displayname',
       'favouritesCount', 'followersCount', 'friendsCount', 'id', 'label',
       'link', 'listedCount', 'location', 'mediaCount', 'profileBannerUrl',
       'profileImageUrl', 'protected', 'rawDescription', 'renderedDescription',
       'statusesCount', 'username', 'verified', 'link.indices', 'link.tcourl',
       'link.text', 'link.url', 'label.badgeUrl', 'label.description',
       'label.longDescription', 'label.url'],
      dtype='object')

In [6]:
embeddings = model.encode(data, show_progress_bar=False)

In [7]:
topic_model.visualize_documents(data, embeddings=embeddings)

In [29]:
from umap import UMAP
from hdbscan import HDBSCAN

reduced_embeddings = UMAP(n_neighbors=15, n_components=5, metric='cosine').fit_transform(embeddings)
hdbscan_model = HDBSCAN(min_cluster_size=10, metric='euclidean', prediction_data=True)
topic_model = BERTopic(hdbscan_model=hdbscan_model,embedding_model=model).fit(data)
topic_model.visualize_documents(data)

2023-04-09 14:28:34,090 - BERTopic - Transformed documents to Embeddings
2023-04-09 14:28:49,438 - BERTopic - Reduced dimensionality
2023-04-09 14:28:49,615 - BERTopic - Clustered reduced embeddings
2023-04-09 14:28:51,886 - BERTopic - Reduced number of topics from 180 to 7


In [19]:
topic_model = BERTopic(hdbscan_model=hdbscan_model,embedding_model=model, n_gram_range=(1,2), min_topic_size=10, nr_topics=10).fit(data)
topic_model.visualize_documents(data)

In [28]:
topic_model.visualize_hierarchy()